# Battle of New York City Neigborhood Lifestyles

Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geopy-1.18.1               |             py_0          51 KB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    ------------------------------------------------------------
                                           Total:          84 KB

The following NEW packages will be INSTALLED:

    geographiclib: 1.49-py_0   conda-forge
    geopy:         1.18.1-py_0 conda-forge


geopy-1.18.1         | 51 KB     | ##################################### | 100% 
geographiclib-1.49   | 32 KB     | ##################################### | 100% 
Preparing transaction: done
Verifying transaction: done
Executing transaction: done
Solving environment: done

## Package Plan ##

  envi

## Download and Explore Dataset

Download New York Geo Data json (can also be found at https://geo.nyu.edu/catalog/nyu_2451_34572)

In [2]:
!wget -q -O 'newyork_data.json' https://ibm.box.com/shared/static/fbpwbovar7lf8p5sgddm06cgipa2rxpe.json
print('Data downloaded!')

Data downloaded!


Load json

In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

Read features in new york data

In [4]:
neighborhoods_data = newyork_data['features']

In [5]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

Notice how all the relevant data is in the features key, which is basically a list of the neighborhoods. So, let's define a new variable that includes this data.

Tranform the data into a *pandas* dataframe

In [12]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [13]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

Lets read the data from neighborhoods data and write to pandas dataframe - neighborhoods

In [14]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [15]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [16]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [17]:
address = 'New York City, NY'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

/home/jupyterlab/conda/lib/python3.6/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


The geograpical coordinate of New York City are 40.7308619, -73.9871558.


Lets create the map with these cordinates and superimpose neighborhoods on it

In [18]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

## Setting up Foursquare API and Credentials

In [173]:
CLIENT_ID = 'xx' # your Foursquare ID
CLIENT_SECRET = 'xx' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: xx
CLIENT_SECRET:xx


In [22]:
neighborhood_latitude = neighborhoods.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = neighborhoods.loc[0, 'Longitude'] # neighborhood longitude value
neighborhood_name = neighborhoods.loc[0, 'Neighborhood'] # neighborhood name

In [174]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=xx&client_secret=xx&v=20180605&ll=40.89470517661,-73.84720052054902&radius=500&limit=100'

Lets see if we can make calls

In [30]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5c296065db04f53ab86f8633'}, 'response': {'suggestedFilters': {'header': 'Tap to show:', 'filters': [{'name': 'Open now', 'key': 'openNow'}]}, 'headerLocation': 'Wakefield', 'headerFullLocation': 'Wakefield, Bronx', 'headerLocationGranularity': 'neighborhood', 'totalResults': 7, 'suggestedBounds': {'ne': {'lat': 40.899205181110005, 'lng': -73.84125857127495}, 'sw': {'lat': 40.89020517211, 'lng': -73.8531424698231}}, 'groups': [{'type': 'Recommended Places', 'name': 'recommended', 'items': [{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4c537892fd2ea593cb077a28', 'name': 'Lollipops Gelato', 'location': {'address': '4120 Baychester Ave', 'crossStreet': 'Edenwald & Bussing Ave', 'lat': 40.894123150205274, 'lng': -73.84589162362325, 'labeledLatLngs': [{'label': 'display', 'lat': 40.894123150205274, 'lng': -73.84589162362325}], 'distance': 127, 'postalC

## Venues in NYC Neighborhoods

Lets define a function to collect venues from returned response

In [31]:
def getNearbyVenues(names, latitudes, longitudes, radius=900):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

We define variable that will gather relavant information and put into 'nyc_venues' dataframe 

In [32]:
nyc_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [33]:
print(nyc_venues.shape)
nyc_venues.head()

(18773, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

                         Venue  Venue Latitude  Venue Longitude  \
0             Lollipops Gelato       40.894123       -73.845892   
1           Ripe Kitchen & Bar       40.898152       -73.838875   
2  Jackie's West Indian Bakery       40.889283       -73.843310   
3                     Rite Aid       40.896521       -73.844680   
4              Ali's Roti Shop       40.894036       -73.856935   

         Venue Category  
0          Dessert Shop  
1  Caribbean Restaurant  
2  Caribbean Restaurant  
3              Pharmacy  
4  Caribbean Restaurant

In [38]:
 nyc_venues.groupby(['Neighborhood']).count().reset_index().tail()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  Venue  \
297    Woodhaven                     62                      62     62   
298     Woodlawn                     47                      47     47   
299      Woodrow                     19                      19     19   
300     Woodside                    100                     100    100   
301    Yorkville                    100                     100    100   

     Venue Latitude  Venue Longitude  Venue Category  
297              62               62              62  
298              47               47              47  
299              19               19              19  
300             100              100             100  
301             100              100             100

Save data incase - locally to avoid API calls when working with CC labs or IBM. They disconnect and you have to make calls again to retrieve data from Foursquare

In [48]:
nyc_venues.to_csv('nyc_venues.csv')

Assign new variable to work with relevant columns.

In [42]:
nyc_data = nyc_venues.filter(['Neighborhood','Neighborhood Latitude','Neighborhood Longitude'], axis=1)

In [43]:
nyc_data.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude
0    Wakefield              40.894705              -73.847201
1    Wakefield              40.894705              -73.847201
2    Wakefield              40.894705              -73.847201
3    Wakefield              40.894705              -73.847201
4    Wakefield              40.894705              -73.847201

Sort table

In [44]:
nyc_data.sort_values("Neighborhood", inplace = True)

Keep unique rows and clean up.

In [45]:
nyc_data.drop_duplicates(subset ="Neighborhood", inplace = True) 

Reset index

In [46]:
nyc_data.reset_index(drop=True)

Neighborhood  Neighborhood Latitude  Neighborhood Longitude
0                     Allerton              40.865788              -73.859319
1                     Annadale              40.538114              -74.178549
2                Arden Heights              40.549286              -74.185887
3                    Arlington              40.635325              -74.165104
4                     Arrochar              40.596313              -74.067124
5                      Arverne              40.589144              -73.791992
6                      Astoria              40.768509              -73.915654
7              Astoria Heights              40.770317              -73.894680
8                   Auburndale              40.761730              -73.791762
9                   Bath Beach              40.599519              -73.998752
10           Battery Park City              40.711932              -74.016869
11                   Bay Ridge              40.625801              -74.030621
12                 Bay Terrace              40.782843              -73.776802
13                  Baychester              40.866858              -73.835798
14                     Bayside              40.766041              -73.774274
15                   Bayswater              40.611322              -73.765968
16                Bedford Park              40.870185              -73.885512
17          Bedford Stuyvesant              40.687232              -73.941785
18                  Beechhurst              40.792781              -73.804365
19                    Bellaire              40.733014              -73.738892
20                Belle Harbor              40.576156              -73.854018
21                   Bellerose              40.728573              -73.720128
22                     Belmont              40.857277              -73.888452
23                 Bensonhurst              40.611009              -73.995180
24                Bergen Beach              40.615150              -73.898556
25                  Blissville              40.737251              -73.932442
26                  Bloomfield              40.605779              -74.187256
27                 Boerum Hill              40.685683              -73.983748
28                Borough Park              40.633131              -73.990498
29                Breezy Point              40.557401              -73.925512
30                   Briarwood              40.710935              -73.811748
31              Brighton Beach              40.576825              -73.965094
32               Broad Channel              40.603027              -73.820055
33           Broadway Junction              40.677861              -73.903317
34                   Bronxdale              40.852723              -73.861726
35            Brooklyn Heights              40.695864              -73.993782
36                  Brookville              40.660003              -73.751753
37                 Brownsville              40.663950              -73.910235
38                  Bulls Head              40.609592              -74.159409
39                    Bushwick              40.698116              -73.925258
40                Butler Manor              40.506082              -74.229504
41             Cambria Heights              40.692775              -73.735269
42                    Canarsie              40.635564              -73.902093
43               Carnegie Hill              40.782683              -73.953256
44             Carroll Gardens              40.680540              -73.994654
45                 Castle Hill              40.819014              -73.848027
46           Castleton Corners              40.613336              -74.119181
47              Central Harlem              40.815976              -73.943211
48                  Charleston              40.530531              -74.232158
49                     Chelsea              40.744035              -74.003116
50                   Chinatown          

Now we have all neighborhoods with their coordinates

In [47]:
nyc_data.shape

(302, 3)

## Removing irrelevant lifestyle venues

Lets look at the venues in neighborhoods again.

In [48]:
nyc_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

                         Venue  Venue Latitude  Venue Longitude  \
0             Lollipops Gelato       40.894123       -73.845892   
1           Ripe Kitchen & Bar       40.898152       -73.838875   
2  Jackie's West Indian Bakery       40.889283       -73.843310   
3                     Rite Aid       40.896521       -73.844680   
4              Ali's Roti Shop       40.894036       -73.856935   

         Venue Category  
0          Dessert Shop  
1  Caribbean Restaurant  
2  Caribbean Restaurant  
3              Pharmacy  
4  Caribbean Restaurant

For our analysis of lifestyle we will remove food and transportation related categories

In [49]:
nyc_venues = nyc_venues[~nyc_venues['Venue Category'].str.contains("Restaurant")]
nyc_venues = nyc_venues[~nyc_venues['Venue Category'].str.contains("Pizza")]
nyc_venues = nyc_venues[~nyc_venues['Venue Category'].str.contains("Deli")]
nyc_venues = nyc_venues[~nyc_venues['Venue Category'].str.contains("Donut")]
nyc_venues = nyc_venues[~nyc_venues['Venue Category'].str.contains("Diner")]
nyc_venues = nyc_venues[~nyc_venues['Venue Category'].str.contains("Bank")]
nyc_venues = nyc_venues[~nyc_venues['Venue Category'].str.contains("Hotel")]
nyc_venues = nyc_venues[~nyc_venues['Venue Category'].str.contains("Intersection")]
nyc_venues = nyc_venues[~nyc_venues['Venue Category'].str.contains("Bus")]
nyc_venues = nyc_venues[~nyc_venues['Venue Category'].str.contains("Train")]
nyc_venues = nyc_venues[~nyc_venues['Venue Category'].str.contains("Sandwich")]
nyc_venues = nyc_venues[~nyc_venues['Venue Category'].str.contains("Joint")]
nyc_venues = nyc_venues[~nyc_venues['Venue Category'].str.contains("Food")]

## Analyze neighborhoods

We will one hot encode each venue

In [50]:
# one hot encoding
nyc_onehot = pd.get_dummies(nyc_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
nyc_onehot['Neighbourhood'] = nyc_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [nyc_onehot.columns[-1]] + list(nyc_onehot.columns[:-1])
nyc_onehot = nyc_onehot[fixed_columns]

nyc_onehot.head()

Neighbourhood  Accessories Store  Adult Boutique  Airport Lounge  \
0     Wakefield                  0               0               0   
3     Wakefield                  0               0               0   
5     Wakefield                  0               0               0   
6     Wakefield                  0               0               0   
9     Wakefield                  0               0               0   

   Airport Service  Airport Terminal  Amphitheater  Animal Shelter  \
0                0                 0             0               0   
3                0                 0             0               0   
5                0                 0             0               0   
6                0                 0             0               0   
9                0                 0             0               0   

   Antique Shop  Aquarium  Arcade  Art Gallery  Art Museum  \
0             0         0       0            0           0   
3             0         0       0            0           0   
5             0         0       0            0           0   
6             0         0       0            0           0   
9             0         0       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Athletics & Sports  Auditorium  \
0                    0                     0                   0           0   
3                    0                     0                   0           0   
5                    0                     0                   0           0   
6                    0                     0                   0           0   
9                    0                     0                   0           0   

   Auto Dealership  Auto Garage  Auto Workshop  Automotive Shop  Bagel Shop  \
0                0            0              0                0           0   
3                0            0              0                0           0   
5                0            0              0                0           0   
6                0            0              0                0           0   
9                0            0              0                0           0   

   Bakery  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0       0    0               0                 0                 0   
3       0    0               0                 0                 0   
5       0    0               0                 0                 0   
6       0    0               0                 0                 0   
9       0    0               0                 0                 0   

   Basketball Stadium  Bath House  Beach  Beach Bar  Bed & Breakfast  \
0                   0           0      0          0                0   
3                   0           0      0          0                0   
5                   0           0      0          0                0   
6                   0           0      0          0                0   
9                   0           0      0          0                0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0         0            0           0              0                         0   
3         0            0           0              0                         0   
5         0            0           0              0                         0   
6         0            0           0              0                         0   
9         0            0           0              0                         0   

   Bike Shop  Bike Trail  Bistro  Board Shop  Boat or Ferry  Bookstore  \
0          0           0       0           0              0          0   
3          0           0       0           0              0          0   
5          0           0       0           0              0          0   
6          0           0       0           0              0          0   
9          0           0       0           0              0          0   

   Border Crossing  Botanical Garden  Boutiqu

In [51]:
nyc_onehot.shape

(10353, 348)

We calculate their frequency compared to other type of venues in each neighborhood by *mean*  and group them

In [52]:
nyc_grouped = nyc_onehot.groupby('Neighbourhood').mean().reset_index()
nyc_grouped

Neighbourhood  Accessories Store  Adult Boutique  \
0                     Allerton           0.000000        0.000000   
1                     Annadale           0.000000        0.000000   
2                Arden Heights           0.000000        0.000000   
3                    Arlington           0.000000        0.000000   
4                     Arrochar           0.000000        0.000000   
5                      Arverne           0.000000        0.000000   
6                      Astoria           0.000000        0.000000   
7              Astoria Heights           0.000000        0.000000   
8                   Auburndale           0.000000        0.000000   
9                   Bath Beach           0.000000        0.000000   
10           Battery Park City           0.000000        0.000000   
11                   Bay Ridge           0.000000        0.000000   
12                 Bay Terrace           0.023256        0.000000   
13                  Baychester           0.042254        0.000000   
14                     Bayside           0.000000        0.000000   
15                   Bayswater           0.000000        0.000000   
16                Bedford Park           0.000000        0.000000   
17          Bedford Stuyvesant           0.000000        0.000000   
18                  Beechhurst           0.000000        0.000000   
19                    Bellaire           0.000000        0.000000   
20                Belle Harbor           0.000000        0.000000   
21                   Bellerose           0.000000        0.000000   
22                     Belmont           0.000000        0.000000   
23                 Bensonhurst           0.000000        0.000000   
24                Bergen Beach           0.000000        0.000000   
25                  Blissville           0.000000        0.000000   
26                  Bloomfield           0.000000        0.000000   
27                 Boerum Hill           0.000000        0.000000   
28                Borough Park           0.000000        0.000000   
29                Breezy Point           0.000000        0.000000   
30                   Briarwood           0.000000        0.000000   
31              Brighton Beach           0.000000        0.000000   
32               Broad Channel           0.000000        0.000000   
33           Broadway Junction           0.000000        0.000000   
34                   Bronxdale           0.000000        0.000000   
35            Brooklyn Heights           0.000000        0.000000   
36                  Brookville           0.000000        0.000000   
37                 Brownsville           0.000000        0.000000   
38                  Bulls Head           0.000000        0.000000   
39                    Bushwick           0.000000        0.000000   
40                Butler Manor           0.000000        0.000000   
41             Cambria Heights           0.000000        0.000000   
42                    Canarsie           0.000000        0.000000   
43               Carnegie Hill           0.000000        0.000000   
44             Carroll Gardens           0.000000        0.000000   
45                 Castle Hill           0.000000        0.000000   
46           Castleton Corners           0.000000        0.000000   
47              Central Harlem           0.000000        0.000000   
48                  Charleston           0.000000        0.000000   
49                     Chelsea           0.000000        0.000000   
50                   Chinatown           0.000000        0.000000   
51                 City Island           0.000000        0.000000   
52                   City Line           0.000000        0.000000   
53                Civic Center           0.000000        0.000000   
54           Claremont Village           0.000000        0.000000   
55                Clason Point           0.000000        0.000000   
56                     Clifton           0.000000        0.000000   
57             

In [79]:
nyc_grouped.shape

(302, 343)

In [53]:
num_top_venues = 5

for hood in nyc_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = nyc_grouped[nyc_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
               venue  freq
0           Pharmacy  0.17
1        Supermarket  0.12
2       Dessert Shop  0.08
3     Breakfast Spot  0.04
4  Mobile Phone Shop  0.04


----Annadale----
               venue  freq
0              Trail  0.22
1               Park  0.11
2       Liquor Store  0.11
3             Bakery  0.11
4  Elementary School  0.11


----Arden Heights----
               venue  freq
0             Lawyer  0.11
1           Pharmacy  0.11
2  Elementary School  0.11
3       Liquor Store  0.11
4          Gift Shop  0.11


----Arlington----
             venue  freq
0      Snack Place  0.17
1   Rental Service  0.17
2    Boat or Ferry  0.17
3  Automotive Shop  0.17
4      Coffee Shop  0.17


----Arrochar----
              venue  freq
0             Beach  0.11
1    Baseball Field  0.11
2      Dance Studio  0.06
3  Sculpture Garden  0.06
4        Steakhouse  0.06


----Arverne----
           venue  freq
0      Surf Spot  0.20
1          Beach  0.15
2  Metro Station  0.10

Define function to sort common venues

In [57]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Targeting 20 most common venues based on their frequency in the neighborhood and creating dataframe

In [151]:
num_top_venues = 20

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = nyc_grouped['Neighbourhood']

for ind in np.arange(nyc_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(nyc_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood         1st Most Common Venue  \
0                     Allerton                      Pharmacy   
1                     Annadale                         Trail   
2                Arden Heights                     Gift Shop   
3                    Arlington                Rental Service   
4                     Arrochar                         Beach   
5                      Arverne                     Surf Spot   
6                      Astoria                           Bar   
7              Astoria Heights           Rental Car Location   
8                   Auburndale                Cosmetics Shop   
9                   Bath Beach                        Bakery   
10           Battery Park City                   Coffee Shop   
11                   Bay Ridge                           Spa   
12                 Bay Terrace                 Women's Store   
13                  Baychester                Clothing Store   
14                     Bayside                           Bar   
15                   Bayswater                    Playground   
16                Bedford Park                   Supermarket   
17          Bedford Stuyvesant                   Coffee Shop   
18                  Beechhurst                      Pharmacy   
19                    Bellaire                          Park   
20                Belle Harbor                         Beach   
21                   Bellerose                 Grocery Store   
22                     Belmont                    Shoe Store   
23                 Bensonhurst                        Bakery   
24                Bergen Beach               Harbor / Marina   
25                  Blissville                        Bakery   
26                  Bloomfield           Sporting Goods Shop   
27                 Boerum Hill                           Bar   
28                Borough Park                    Kids Store   
29                Breezy Point                     Surf Spot   
30                   Briarwood                   Coffee Shop   
31              Brighton Beach                         Beach   
32               Broad Channel                     Surf Spot   
33           Broadway Junction                Discount Store   
34                   Bronxdale                   Coffee Shop   
35            Brooklyn Heights                          Park   
36                  Brookville                          Park   
37                 Brownsville                Discount Store   
38                  Bulls Head                Baseball Field   
39                    Bushwick                           Bar   
40                Butler Manor                Baseball Field   
41             Cambria Heights                      Pharmacy   
42                    Canarsie                 Grocery Store   
43               Carnegie Hill                          Café   
44             Carroll Gardens                   Coffee Shop   
45                 Castle Hill                   Supermarket   
46           Castleton Corners                Ice Cream Shop   
47              Central Harlem                          Café   
48                  Charleston                    Shoe Store   
49                     Chelsea                   Art Gallery   
50                   Chinatown                Ice Cream Shop   
51                 City Island               Harbor / Marina   
52                   City Line                   Supermarket   
53                Civic Center                   Coffee Shop   
54           Claremont Village                Discount Store   
55                Clason Point                          Park   
56                     Clifton                Cosmetics Shop   
57                     Clinton                       Theater   
58                Clinton Hill                   Coffee Shop   
59                  Co-op City                    Shoe Store   
60                 Cobble Hill                           Bar   
61               College Point                    

In [163]:
# set number of clusters
kclusters = 4

nyc_grouped_clustering = nyc_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(nyc_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 2, 0, 2, 1, 1, 2, 0, 0, 2], dtype=int32)

Verify two dataframe shapes to avoid error in merging

In [164]:
kmeans.labels_.shape

(302,)

In [165]:
nyc_data.shape

(302, 4)

Since they are of same size and sorted ascending we merge nyc_data table consists of neighborhood lat, long with 20 most commmon places dataset neighborhoods_venues_sorted adding cluster labels.

In [166]:
nyc_merged = nyc_data

# add clustering labels
nyc_merged['Cluster Labels'] = kmeans.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
nyc_merged = nyc_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

nyc_merged.head() # check the last columns!

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
18378       Allerton              40.865788              -73.859319   
14226       Annadale              40.538114              -74.178549   
15188  Arden Heights              40.549286              -74.185887   
14717      Arlington              40.635325              -74.165104   
14740       Arrochar              40.596313              -74.067124   

       Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
18378               0              Pharmacy           Supermarket   
14226               2                 Trail            Sports Bar   
15188               0             Gift Shop          Liquor Store   
14717               2        Rental Service         Boat or Ferry   
14740               1                 Beach        Baseball Field   

      3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
18378          Dessert Shop               Brewery                   Bar   
14226                Bakery          Home Service     Elementary School   
15188              Pharmacy         Shopping Mall         Moving Target   
14717       Automotive Shop           Coffee Shop        Nightlife Spot   
14740           Supermarket            Bagel Shop             Juice Bar   

      6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
18378         Metro Station     Martial Arts Dojo            Smoke Shop   
14226          Liquor Store                  Park          Dessert Shop   
15188           Coffee Shop                   Spa     Elementary School   
14717           Snack Place              Fountain      Football Stadium   
14740          Dance Studio      Department Store            Playground   

      9th Most Common Venue 10th Most Common Venue   11th Most Common Venue  \
18378                   Spa       Basketball Court               Playground   
14226           Fish Market         Farmers Market              Event Space   
15188                Lawyer      Fish & Chips Shop                     Farm   
14717               Exhibit            Fabric Shop  Fruit & Vegetable Store   
14740      Sculpture Garden                   Park               Steakhouse   

      12th Most Common Venue 13th Most Common Venue 14th Most Common Venue  \
18378      Mobile Phone Shop         Clothing Store       Department Store   
14226               Fountain                Exhibit            Fabric Shop   
15188                Exhibit       Football Stadium            Fabric Shop   
14717                Factory                   Farm         Farmers Market   
14740             Taco Place          Moving Target             Toll Plaza   

      15th Most Common Venue 16th Most Common Venue 17th Most Common Venue  \
18378           Dance Studio         Cosmetics Shop         Breakfast Spot   
14226                Factory                   Farm                  Field   
15188            Flower Shop            Flea Market                Factory   
14717                  Field     Frozen Yogurt Shop            Film Studio   
14740         Cosmetics Shop         Ice Cream Shop         History Museum   

           18th Most Common Venue      19th Most Common Venue  \
18378                  Shoe Store              Farmers Market   
14226               Fishing Store            Football Stadium   
15188               Fishing Store  Financial or Legal Service   
14717  Financial or Legal Service                 Event Space   
14740                        Farm           Electronics Store   

      20th Most Common Venue  
18378                   Farm  
14226            Film Studio  
15188         Farmers Market  
14717            Fish Market  
14740      Elementary School

In [167]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(nyc_merged['Neighborhood Latitude'], nyc_merged['Neighborhood Longitude'], nyc_merged['Neighborhood'], nyc_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

#### 1st CLUSTER

The Technician neighborhood

In [168]:
nyc_merged.loc[nyc_merged['Cluster Labels'] == 0, nyc_merged.columns[[1] + list(range(0, nyc_merged.shape[1]))]]

Neighborhood Latitude         Neighborhood  Neighborhood Latitude  \
18378              40.865788             Allerton              40.865788   
15188              40.549286        Arden Heights              40.549286   
16418              40.770317      Astoria Heights              40.770317   
11477              40.761730           Auburndale              40.761730   
12476              40.782843          Bay Terrace              40.782843   
659                40.866858           Baychester              40.866858   
760                40.870185         Bedford Park              40.870185   
12429              40.792781           Beechhurst              40.792781   
13390              40.733014             Bellaire              40.733014   
11706              40.728573            Bellerose              40.728573   
2679               40.611009          Bensonhurst              40.611009   
15325              40.605779           Bloomfield              40.605779   
5301               40.633131         Borough Park              40.633131   
3067               40.576825       Brighton Beach              40.576825   
17698              40.677861    Broadway Junction              40.677861   
18280              40.852723            Bronxdale              40.852723   
3778               40.663950          Brownsville              40.663950   
15353              40.609592           Bulls Head              40.609592   
15124              40.506082         Butler Manor              40.506082   
12226              40.692775      Cambria Heights              40.692775   
4950               40.635564             Canarsie              40.635564   
2306               40.819014          Castle Hill              40.819014   
13957              40.613336    Castleton Corners              40.613336   
15138              40.530531           Charleston              40.530531   
6031               40.678570            City Line              40.678570   
15855              40.619178              Clifton              40.619178   
95                 40.874294           Co-op City              40.874294   
11327              40.784903        College Point              40.784903   
15896              40.604473              Concord              40.604473   
2431               40.834284            Concourse              40.834284   
16483              40.824780    Concourse Village              40.824780   
5104               40.574293         Coney Island              40.574293   
10138              40.742382               Corona              40.742382   
4802               40.682391        Cypress Hills              40.682391   
14894              40.588673         Dongan Hills              40.588673   
3449               40.641718        East Flatbush              40.641718   
1072               40.842696         East Tremont              40.842696   
144                40.887556          Eastchester              40.887556   
2552               40.884561             Edenwald              40.884561   
16002              40.630147             Elm Park              40.630147   
14197              40.542231          Eltingville              40.542231   
18448              40.646926              Erasmus              40.646926   
12288              40.603134         Far Rockaway              40.603134   
5001               40.630446            Flatlands              40.630446   
12773              40.741378          Floral Park              40.741378   
963                40.860997              Fordham              40.860997   
11835              40.734394        Fresh Meadows              40.734394   
6264               40.623845           Georgetown              40.623845   
5463               40.590848      Gerritsen Beach              40.590848   
11700              40.749441            Glen Oaks              40.749441   
10980              40.702762             Glendale              40.702762   
14708              40.620172         Graniteville      

#### 2nd CLUSTER

The Adventurer’s neighborhood

In [169]:
nyc_merged.loc[nyc_merged['Cluster Labels'] == 1, nyc_merged.columns[[1] + list(range(0, nyc_merged.shape[1]))]]

Neighborhood Latitude     Neighborhood  Neighborhood Latitude  \
14740              40.596313         Arrochar              40.596313   
12555              40.589144          Arverne              40.589144   
18650              40.611322        Bayswater              40.611322   
13282              40.576156     Belle Harbor              40.576156   
6066               40.615150     Bergen Beach              40.615150   
12325              40.557401     Breezy Point              40.557401   
12308              40.603027    Broad Channel              40.603027   
724                40.847247      City Island              40.847247   
18619              40.587338          Hammels              40.587338   
15966              40.638433     Howland Hook              40.638433   
5087               40.577914  Manhattan Beach              40.577914   
14931              40.573527    Midland Beach              40.573527   
12652              40.572037         Neponsit              40.572037   
12581              40.582802   Rockaway Beach              40.582802   
13310              40.580343    Rockaway Park              40.580343   
17933              40.567376          Roxbury              40.567376   
5643               40.576375         Sea Gate              40.576375   
13863              40.580247      South Beach              40.580247   
1586               40.815109      Throgs Neck              40.815109   
17874              40.603707      Willowbrook              40.603707   

       Neighborhood Longitude  Cluster Labels 1st Most Common Venue  \
14740              -74.067124               1                 Beach   
12555              -73.791992               1             Surf Spot   
18650              -73.765968               1            Playground   
13282              -73.854018               1                 Beach   
6066               -73.898556               1       Harbor / Marina   
12325              -73.925512               1             Surf Spot   
12308              -73.820055               1             Surf Spot   
724                -73.786488               1       Harbor / Marina   
18619              -73.805530               1                 Beach   
15966              -74.186223               1       Harbor / Marina   
5087               -73.943537               1       Harbor / Marina   
14931              -74.093483               1                 Beach   
12652              -73.857547               1                 Beach   
12581              -73.822361               1                 Beach   
13310              -73.841534               1                 Beach   
17933              -73.892138               1                 Beach   
5643               -74.007873               1                 Beach   
13863              -74.079553               1                  Pier   
1586               -73.816350               1                   Bar   
17874              -74.132084               1         Moving Target   

      2nd Most Common Venue          3rd Most Common Venue  \
14740        Baseball Field                    Supermarket   
12555                 Beach                  Metro Station   
18650                 Beach                           Park   
13282              Boutique                            Spa   
6066                Stables                            Gym   
12325            Lighthouse                          Beach   
12308              Dive Bar                Other Nightlife   
724                    Park         Thrift / Vintage Store   
18619             Surf Spot                    Supermarket   
15966                Lounge                         Resort   
5087           Dessert Shop                            Bar   
14931        Baseball Field            Rental Car Location   
12652                  Park                    Zoo Exhibit   
12581                   Bar                  Boat or Ferry   
13310              Pharmacy                     Bagel Shop   
17933     

#### 3rd CLUSTER

The Socialite’s neighborhood 

In [170]:
nyc_merged.loc[nyc_merged['Cluster Labels'] == 2, nyc_merged.columns[[1] + list(range(0, nyc_merged.shape[1]))]]

Neighborhood Latitude               Neighborhood  \
14226              40.538114                   Annadale   
14717              40.635325                  Arlington   
9704               40.768509                    Astoria   
5275               40.599519                 Bath Beach   
9484               40.711932          Battery Park City   
2596               40.625801                  Bay Ridge   
11436              40.766041                    Bayside   
4105               40.687232         Bedford Stuyvesant   
1973               40.857277                    Belmont   
17361              40.737251                 Blissville   
5818               40.685683                Boerum Hill   
11857              40.710935                  Briarwood   
4173               40.695864           Brooklyn Heights   
3988               40.698116                   Bushwick   
15446              40.782683              Carnegie Hill   
4340               40.680540            Carroll Gardens   
7313               40.815976             Central Harlem   
8397               40.744035                    Chelsea   
6820               40.715618                  Chinatown   
15619              40.715229               Civic Center   
8134               40.759101                    Clinton   
5552               40.693229               Clinton Hill   
4302               40.687920                Cobble Hill   
1634               40.844246               Country Club   
3447               40.670829              Crown Heights   
14395              40.643675                Ditmas Park   
11647              40.766846                 Douglaston   
5673               40.690844                   Downtown   
17743              40.703176                      Dumbo   
5367               40.619219              Dyker Heights   
10711              40.764073              East Elmhurst   
7418               40.792249                East Harlem   
8555               40.727847               East Village   
6305               40.708492          East Williamsburg   
2281               40.821986             Edgewater Park   
9991               40.744049                   Elmhurst   
198                40.895437                  Fieldston   
9551               40.707107         Financial District   
3352               40.636326                   Flatbush   
17161              40.739673                   Flatiron   
10466              40.764454                   Flushing   
10247              40.725264               Forest Hills   
13595              40.714611       Forest Hills Gardens   
4678               40.688527                Fort Greene   
6712               40.614768              Fort Hamilton   
17498              40.703281               Fulton Ferry   
4533               40.673931                    Gowanus   
9407               40.737210                   Gramercy   
2894               40.730201                 Greenpoint   
8536               40.726933          Greenwich Village   
7083               40.823604           Hamilton Heights   
18511              40.756658               Hudson Yards   
16793              40.743414              Hunters Point   
1448               40.809730                Hunts Point   
7042               40.867684                     Inwood   
9946               40.751981            Jackson Heights   
3481               40.642382                 Kensington   
10342              40.705179                Kew Gardens   
330                40.881687                Kingsbridge   
18419              40.870392        Kingsbridge Heights   
7679               40.768113                 Lenox Hill   
18082              40.576506            Lighthouse Hill   
7973               40.773529             Lincoln Square   
8947               40.719324               Little Italy   
11547              40.770826                Little Neck   
10519              40.750217           Long Island City   
8679               40.717807            Lower East Sid

#### 4th CLUSTER

The Provider’s neighborhood 

In [171]:
nyc_merged.loc[nyc_merged['Cluster Labels'] == 3, nyc_merged.columns[[1] + list(range(0, nyc_merged.shape[1]))]]

Neighborhood Latitude         Neighborhood  Neighborhood Latitude  \
13371              40.660003           Brookville              40.660003   
16437              40.831428    Claremont Village              40.831428   
1580               40.806551         Clason Point              40.806551   
4881               40.669926        East New York              40.669926   
12511              40.595642             Edgemere              40.595642   
17915              40.579119          Egbertville              40.579119   
15918              40.606794         Emerson Hill              40.606794   
18759              40.617311            Fox Hills              40.617311   
13852              40.624185          Grymes Hill              40.624185   
15094              40.531912             Huguenot              40.531912   
13160              40.667884            Laurelton              40.667884   
18154              40.790602                Malba              40.790602   
18070              40.526264         Prince's Bay              40.526264   
12186              40.666230  Springfield Gardens              40.666230   
2096               40.881395       Spuyten Duyvil              40.881395   
13854              40.597069            Todt Hill              40.597069   
14024              40.586314               Travis              40.586314   

       Neighborhood Longitude  Cluster Labels 1st Most Common Venue  \
13371              -73.751753               3                  Park   
16437              -73.901199               3        Discount Store   
1580               -73.854144               3                  Park   
4881               -73.880699               3           Yoga Studio   
12511              -73.776133               3                  Park   
17915              -74.127272               3            Bagel Shop   
15918              -74.097762               3                Market   
18759              -74.081740               3                  Park   
13852              -74.087248               3                  Park   
15094              -74.191741               3        Ice Cream Shop   
13160              -73.740256               3        Cosmetics Shop   
18154              -73.826678               3                  Park   
18070              -74.201526               3            Bagel Shop   
12186              -73.760421               3                  Park   
2096               -73.917190               3                  Park   
13854              -74.111329               3              Mountain   
14024              -74.190737               3         Bowling Alley   

      2nd Most Common Venue 3rd Most Common Venue       4th Most Common Venue  \
13371                  Lake                Bakery                  Laundromat   
16437        Ice Cream Shop                   Gym                        Park   
1580         Discount Store         Boat or Ferry              Scenic Lookout   
4881          Grocery Store                  Park            Video Game Store   
12511         Metro Station           Supermarket                  Skate Park   
17915        Cosmetics Shop        Clothing Store              History Museum   
15918            Bagel Shop       Automotive Shop                        Park   
18759        Cosmetics Shop              Pharmacy               Grocery Store   
13852      Basketball Court            Playground                     Dog Run   
15094           Bridal Shop                  Park                         Spa   
13160                  Park              Pharmacy                 Supermarket   
18154        Discount Store                   Gym                   Rest Area   
18070              Pharmacy                  Park  Financial or Legal Service   
12186        Discount Store            Laundromat                         Gym   
2096               Pharmacy            Bagel Shop              Cosmetics Shop   
13854                  Park           Golf Course              